In [7]:
import pandas as pd
import numpy as np
import lightgbm as lgb
from hyperopt import fmin, tpe, STATUS_OK, STATUS_FAIL, Trials, hp
from sklearn.metrics import auc

from sklearn.model_selection import train_test_split

data = pd.read_csv('/Users/shinbo/ML/data/santander-customer-transaction-prediction/train.csv')
X = data.drop(columns=['ID_code','target'])
y = data['target']

In [8]:
data['target'].value_counts()

0    179902
1     20098
Name: target, dtype: int64

In [45]:
SEARCH_PARAMS = {'learning_rate': 0.1,
                 'max_depth': -1,
                 'boosting': 'gbdt'}

FIXED_PARAMS={'objective': 'binary',
              'metric': 'auc',
              'is_unbalance': True,
              'num_boost_round':300,
              'early_stopping_rounds':30}

X_train, X_valid, y_train, y_valid = train_test_split(X, y, test_size=0.2, random_state=1234)
train_data = lgb.Dataset(X_train, label=y_train)
valid_data = lgb.Dataset(X_valid, label=y_valid, reference=train_data)


def objective(SEARCH_PARAMS):
    params = {'metric':FIXED_PARAMS['metric'],
         'objective':FIXED_PARAMS['objective'],
         'is_unbalance':FIXED_PARAMS['is_unbalance'],
         'num_boost_round':FIXED_PARAMS['num_boost_round'],
          'early_stopping_rounds':FIXED_PARAMS['early_stopping_rounds'],
         **SEARCH_PARAMS}

    model = lgb.train(params, train_data,                     
                     valid_sets=[valid_data],
                     num_boost_round=FIXED_PARAMS['num_boost_round'],
                     early_stopping_rounds=FIXED_PARAMS['early_stopping_rounds'],
                     valid_names=['valid'])

    score = model.best_score['valid']['auc']
    
    return -1.0 * score

def objective_final_tuning(SEARCH_PARAMS):
    params = {'metric':FIXED_PARAMS['metric'],
             'objective':FIXED_PARAMS['objective'],
             'is_unbalance':FIXED_PARAMS['is_unbalance'],
              'early_stopping_rounds': round(SEARCH_PARAMS['num_boost_round']/10),
             **TUNED_PARAMS,
             **SEARCH_PARAMS}
    
    model = lgb.train(params, train_data,                     
                     valid_sets=[valid_data],
                     valid_names=['valid'])

    score = model.best_score['valid']['auc']
    
    return -1.0 * score

# lgbm parameters
lgbm_space = {
        "max_depth": hp.choice("max_depth", range(1,20)),
        "num_leaves": hp.choice('num_leaves', range(10, 200)),
        "feature_fraction": hp.quniform("feature_fraction", 0.5, 1.0, 0.1),
        "bagging_fraction": hp.quniform("bagging_fraction", 0.5, 1.0, 0.1),
        "bagging_freq": hp.choice("bagging_freq", np.linspace(0, 50, 10, dtype=int)),
        "reg_alpha": hp.uniform("reg_alpha", 0, 1),
        "reg_lambda": hp.uniform("reg_lambda", 0, 1),
        "min_child_weight": hp.uniform('min_child_weight', 0.5, 10)
    }

final_lgbm_space = {
        "learning_rate": hp.loguniform("learning_rate", np.log(0.01), np.log(0.5)),
        "num_boost_round": hp.choice('num_boost_round', range(100, 3001))
    }

In [46]:
# baseline model
basemodel = lgb.train(FIXED_PARAMS,
                     train_data,                     
                     valid_sets=[valid_data],
                     valid_names=['valid']
                     )

[1]	valid's auc: 0.675146
Training until validation scores don't improve for 30 rounds
[2]	valid's auc: 0.703952
[3]	valid's auc: 0.725887
[4]	valid's auc: 0.738542
[5]	valid's auc: 0.745836
[6]	valid's auc: 0.757384
[7]	valid's auc: 0.764364
[8]	valid's auc: 0.770123
[9]	valid's auc: 0.776088
[10]	valid's auc: 0.781966
[11]	valid's auc: 0.784217
[12]	valid's auc: 0.787797
[13]	valid's auc: 0.791288
[14]	valid's auc: 0.795545
[15]	valid's auc: 0.798036
[16]	valid's auc: 0.801319
[17]	valid's auc: 0.804162
[18]	valid's auc: 0.807839
[19]	valid's auc: 0.809902
[20]	valid's auc: 0.812406
[21]	valid's auc: 0.813674
[22]	valid's auc: 0.816164
[23]	valid's auc: 0.818079
[24]	valid's auc: 0.820099
[25]	valid's auc: 0.821679
[26]	valid's auc: 0.823069
[27]	valid's auc: 0.824274
[28]	valid's auc: 0.825808
[29]	valid's auc: 0.827193
[30]	valid's auc: 0.829244
[31]	valid's auc: 0.830969
[32]	valid's auc: 0.832381
[33]	valid's auc: 0.833144
[34]	valid's auc: 0.833616
[35]	valid's auc: 0.835034
[36

[296]	valid's auc: 0.890622
[297]	valid's auc: 0.890741
[298]	valid's auc: 0.890785
[299]	valid's auc: 0.890737
[300]	valid's auc: 0.890741
Did not meet early stopping. Best iteration is:
[298]	valid's auc: 0.890785


In [50]:
# parameter tuning with fixed other parameters
TUNED_PARAMS = fmin(objective,lgbm_space,
                        algo=tpe.suggest,max_evals=50)

[1]	valid's auc: 0.65016                              
Training until validation scores don't improve for 30 rounds
[2]	valid's auc: 0.685613                             
[3]	valid's auc: 0.704163                             
[4]	valid's auc: 0.716378                             
[5]	valid's auc: 0.730245                             
[6]	valid's auc: 0.738209                             
[7]	valid's auc: 0.744727                             
[8]	valid's auc: 0.750701                             
[9]	valid's auc: 0.755881                             
[10]	valid's auc: 0.761782                            
[11]	valid's auc: 0.766673                            
[12]	valid's auc: 0.769953                            
[13]	valid's auc: 0.77247                             
[14]	valid's auc: 0.774913                            
[15]	valid's auc: 0.779305                            
[16]	valid's auc: 0.782095                            
[17]	valid's auc: 0.784186                            
[18]

[148]	valid's auc: 0.864636                           
[149]	valid's auc: 0.864878                           
[150]	valid's auc: 0.864845                           
[151]	valid's auc: 0.864883                           
[152]	valid's auc: 0.864988                           
[153]	valid's auc: 0.865003                           
[154]	valid's auc: 0.865224                           
[155]	valid's auc: 0.865322                           
[156]	valid's auc: 0.865542                           
[157]	valid's auc: 0.865873                           
[158]	valid's auc: 0.865872                           
[159]	valid's auc: 0.866035                           
[160]	valid's auc: 0.866116                           
[161]	valid's auc: 0.866379                           
[162]	valid's auc: 0.86667                            
[163]	valid's auc: 0.866998                           
[164]	valid's auc: 0.867177                           
[165]	valid's auc: 0.867384                           
[166]	vali

[296]	valid's auc: 0.876266                           
[297]	valid's auc: 0.876288                           
[298]	valid's auc: 0.876293                           
[299]	valid's auc: 0.876283                           
[300]	valid's auc: 0.876274                           
Did not meet early stopping. Best iteration is:       
[298]	valid's auc: 0.876293
[1]	valid's auc: 0.676524                                                        
Training until validation scores don't improve for 30 rounds                     
[2]	valid's auc: 0.710774                                                        
[3]	valid's auc: 0.729522                                                        
[4]	valid's auc: 0.741923                                                        
[5]	valid's auc: 0.756406                                                        
[6]	valid's auc: 0.765597                                                        
[7]	valid's auc: 0.772976                                           

[95]	valid's auc: 0.872572                                                       
[96]	valid's auc: 0.872904                                                       
[97]	valid's auc: 0.873203                                                       
[98]	valid's auc: 0.873363                                                       
[99]	valid's auc: 0.873845                                                       
[100]	valid's auc: 0.874067                                                      
[101]	valid's auc: 0.874379                                                      
[102]	valid's auc: 0.874647                                                      
[103]	valid's auc: 0.874954                                                      
[104]	valid's auc: 0.875386                                                      
[105]	valid's auc: 0.8757                                                        
[106]	valid's auc: 0.875836                                                      
[107]	valid's au

[194]	valid's auc: 0.882746                                                      
[195]	valid's auc: 0.882724                                                      
[196]	valid's auc: 0.882717                                                      
[197]	valid's auc: 0.882702                                                      
[198]	valid's auc: 0.882737                                                      
[199]	valid's auc: 0.882744                                                      
[200]	valid's auc: 0.882739                                                      
[201]	valid's auc: 0.882677                                                      
[202]	valid's auc: 0.882588                                                      
[203]	valid's auc: 0.882677                                                      
[204]	valid's auc: 0.882738                                                      
[205]	valid's auc: 0.882811                                                      
[206]	valid's au

...

[154]	valid's auc: 0.873773                                                       
[155]	valid's auc: 0.873793                                                       
[156]	valid's auc: 0.873911                                                       
[157]	valid's auc: 0.873991                                                       
[158]	valid's auc: 0.874229                                                       
[159]	valid's auc: 0.874336                                                       
[160]	valid's auc: 0.874441                                                       
[161]	valid's auc: 0.874511                                                       
[162]	valid's auc: 0.874628                                                       
[163]	valid's auc: 0.874729                                                       
[164]	valid's auc: 0.874832                                                       
[165]	valid's auc: 0.875061                                                       
[166

[252]	valid's auc: 0.881799                                                       
[253]	valid's auc: 0.881817                                                       
[254]	valid's auc: 0.881885                                                       
[255]	valid's auc: 0.881946                                                       
[256]	valid's auc: 0.881985                                                       
[257]	valid's auc: 0.88201                                                        
[258]	valid's auc: 0.881946                                                       
[259]	valid's auc: 0.881943                                                       
[260]	valid's auc: 0.882111                                                       
[261]	valid's auc: 0.882076                                                       
[262]	valid's auc: 0.882066                                                       
[263]	valid's auc: 0.882194                                                       
[264

[48]	valid's auc: 0.852679                                                        
[49]	valid's auc: 0.853473                                                        
[50]	valid's auc: 0.854008                                                        
[51]	valid's auc: 0.854719                                                        
[52]	valid's auc: 0.855244                                                        
[53]	valid's auc: 0.855562                                                        
[54]	valid's auc: 0.856041                                                        
[55]	valid's auc: 0.857046                                                        
[56]	valid's auc: 0.857686                                                        
[57]	valid's auc: 0.858376                                                        
[58]	valid's auc: 0.858971                                                        
[59]	valid's auc: 0.85948                                                         
[60]

[146]	valid's auc: 0.882883                                                       
[147]	valid's auc: 0.883053                                                       
[148]	valid's auc: 0.883139                                                       
[149]	valid's auc: 0.883315                                                       
[150]	valid's auc: 0.883408                                                       
[151]	valid's auc: 0.883651                                                       
[152]	valid's auc: 0.883864                                                       
[153]	valid's auc: 0.884031                                                       
[154]	valid's auc: 0.8841                                                         
[155]	valid's auc: 0.884131                                                       
[156]	valid's auc: 0.884265                                                       
[157]	valid's auc: 0.884238                                                       
[158

[244]	valid's auc: 0.889531                                                       
[245]	valid's auc: 0.889572                                                       
[246]	valid's auc: 0.889575                                                       
[247]	valid's auc: 0.889581                                                       
[248]	valid's auc: 0.88967                                                        
[249]	valid's auc: 0.889717                                                       
[250]	valid's auc: 0.889755                                                       
[251]	valid's auc: 0.88969                                                        
[252]	valid's auc: 0.889719                                                       
[253]	valid's auc: 0.889785                                                       
[254]	valid's auc: 0.889786                                                       
[255]	valid's auc: 0.88983                                                        
[256

In [51]:
final_model = fmin(objective_final_tuning,final_lgbm_space,
                        algo=tpe.suggest,max_evals=50)

[1]	valid's auc: 0.668639                             
Training until validation scores don't improve for 195 rounds
[2]	valid's auc: 0.701783                             
[3]	valid's auc: 0.723208                             
[4]	valid's auc: 0.736709                             
[5]	valid's auc: 0.751048                             
[6]	valid's auc: 0.759969                             
[7]	valid's auc: 0.769188                             
[8]	valid's auc: 0.77571                              
[9]	valid's auc: 0.782426                             
[10]	valid's auc: 0.789723                            
[11]	valid's auc: 0.795398                            
[12]	valid's auc: 0.799963                            
[13]	valid's auc: 0.804746                            
[14]	valid's auc: 0.808165                            
[15]	valid's auc: 0.811115                            
[16]	valid's auc: 0.814057                            
[17]	valid's auc: 0.816392                            
[18

[148]	valid's auc: 0.877329                           
[149]	valid's auc: 0.877268                           
[150]	valid's auc: 0.877228                           
[151]	valid's auc: 0.877128                           
[152]	valid's auc: 0.877269                           
[153]	valid's auc: 0.877122                           
[154]	valid's auc: 0.877039                           
[155]	valid's auc: 0.877053                           
[156]	valid's auc: 0.877078                           
[157]	valid's auc: 0.877047                           
[158]	valid's auc: 0.877028                           
[159]	valid's auc: 0.87702                            
[160]	valid's auc: 0.876762                           
[161]	valid's auc: 0.876757                           
[162]	valid's auc: 0.8767                             
[163]	valid's auc: 0.876734                           
[164]	valid's auc: 0.876715                           
[165]	valid's auc: 0.876613                           
[166]	vali

[296]	valid's auc: 0.870085                           
[297]	valid's auc: 0.870066                           
[298]	valid's auc: 0.870103                           
[299]	valid's auc: 0.87011                            
[300]	valid's auc: 0.870002                           
[301]	valid's auc: 0.869809                           
[302]	valid's auc: 0.8699                             
[303]	valid's auc: 0.869875                           
[304]	valid's auc: 0.869941                           
[305]	valid's auc: 0.870022                           
[306]	valid's auc: 0.870088                           
[307]	valid's auc: 0.86997                            
[308]	valid's auc: 0.869925                           
[309]	valid's auc: 0.869812                           
[310]	valid's auc: 0.869781                           
[311]	valid's auc: 0.869741                           
[312]	valid's auc: 0.869861                           
Early stopping, best iteration is:                    
[117]	vali

[87]	valid's auc: 0.823243                                                       
[88]	valid's auc: 0.823862                                                       
[89]	valid's auc: 0.824259                                                       
[90]	valid's auc: 0.824681                                                       
[91]	valid's auc: 0.825047                                                       
[92]	valid's auc: 0.825391                                                       
[93]	valid's auc: 0.825638                                                       
[94]	valid's auc: 0.8259                                                         
[95]	valid's auc: 0.82615                                                        
[96]	valid's auc: 0.826774                                                       
[97]	valid's auc: 0.827162                                                       
[98]	valid's auc: 0.827689                                                       
[99]	valid's auc

[25]	valid's auc: 0.833338                                                       
[26]	valid's auc: 0.835222                                                       
[27]	valid's auc: 0.836678                                                       
[28]	valid's auc: 0.838522                                                       
[29]	valid's auc: 0.840395                                                       
[30]	valid's auc: 0.842138                                                       
[31]	valid's auc: 0.843343                                                       
[32]	valid's auc: 0.844656                                                       
[33]	valid's auc: 0.845509                                                       
[34]	valid's auc: 0.846406                                                       
[35]	valid's auc: 0.84733                                                        
[36]	valid's auc: 0.84762                                                        
[37]	valid's auc

...

[160]	valid's auc: 0.879171                                                      
[161]	valid's auc: 0.87919                                                       
[162]	valid's auc: 0.879309                                                      
[163]	valid's auc: 0.879455                                                      
[164]	valid's auc: 0.879433                                                      
[165]	valid's auc: 0.879473                                                      
[166]	valid's auc: 0.879636                                                      
[167]	valid's auc: 0.879641                                                      
[168]	valid's auc: 0.879755                                                      
[169]	valid's auc: 0.87987                                                       
[170]	valid's auc: 0.880024                                                      
[171]	valid's auc: 0.880198                                                      
[172]	valid's au

[259]	valid's auc: 0.888273                                                      
[260]	valid's auc: 0.888273                                                      
[261]	valid's auc: 0.888288                                                      
[262]	valid's auc: 0.888356                                                      
[263]	valid's auc: 0.888351                                                      
[264]	valid's auc: 0.888425                                                      
[265]	valid's auc: 0.888492                                                      
[266]	valid's auc: 0.888555                                                      
[267]	valid's auc: 0.888607                                                      
[268]	valid's auc: 0.888689                                                      
[269]	valid's auc: 0.888715                                                      
[270]	valid's auc: 0.888712                                                      
[271]	valid's au

[358]	valid's auc: 0.892427                                                      
[359]	valid's auc: 0.892448                                                      
[360]	valid's auc: 0.892502                                                      
[361]	valid's auc: 0.892514                                                      
[362]	valid's auc: 0.892501                                                      
[363]	valid's auc: 0.892477                                                      
[364]	valid's auc: 0.892488                                                      
[365]	valid's auc: 0.892561                                                      
[366]	valid's auc: 0.892568                                                      
[367]	valid's auc: 0.892618                                                      
[368]	valid's auc: 0.892622                                                      
[369]	valid's auc: 0.892663                                                      
[370]	valid's au

[457]	valid's auc: 0.89391                                                       
[458]	valid's auc: 0.893894                                                      
[459]	valid's auc: 0.893893                                                      
[460]	valid's auc: 0.89388                                                       
[461]	valid's auc: 0.893873                                                      
[462]	valid's auc: 0.89386                                                       
[463]	valid's auc: 0.893862                                                      
[464]	valid's auc: 0.8939                                                        
[465]	valid's auc: 0.893908                                                      
[466]	valid's auc: 0.893921                                                      
[467]	valid's auc: 0.893948                                                      
[468]	valid's auc: 0.893927                                                      
[469]	valid's au

[556]	valid's auc: 0.893764                                                      
[557]	valid's auc: 0.893704                                                      
[558]	valid's auc: 0.893729                                                      
[559]	valid's auc: 0.893743                                                      
[560]	valid's auc: 0.893707                                                      
[561]	valid's auc: 0.893706                                                      
[562]	valid's auc: 0.893693                                                      
[563]	valid's auc: 0.893739                                                      
[564]	valid's auc: 0.893715                                                      
[565]	valid's auc: 0.893686                                                      
[566]	valid's auc: 0.893661                                                      
[567]	valid's auc: 0.89363                                                       
[568]	valid's au